## Problem Statement

As a part of the recruitment process, we ask all candidates to solve an open-ended problem to give us an opportunity to better understand their approach to problem solving, technical skills etc. Please spend up to a week on the following problem. We should also mention that we encourage the candidate to communicate with us throughout the process, giving us updates and asking questions as necessary. 

Healthcare Dataset Challenge: The task is to **analyze the clinical and financial data of patients hospitalized for a certain condition**. It is attached with this email. Some variable names and patient_id's have been anonymized in this dataset. You are required to **join the data given in different tables**, and **find insights about the drivers of cost of care**. Please see attached documents for datasets. 

For this challenge, you will be given 1-1.5 weeks, at the end of which we expect you to **share your code (github repository) and a document/slides describing your approach and results, insights etc**. This position requires **strong communication and visualization skills**. Your **slide design, narrative and content as well your presentation will be judged not only for technical but communication skills as well**. If you have any question, please feel free to contact Abhijit Ghosh (abhijit.ghosh@holmusk.com).


- analyze the clinical and financial data of patients hospitalized for a certain condition
- join the data given in different tables
- find insights about the drivers of cost of care

In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
warnings.filterwarnings("ignore")

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
plt.style.use('fivethirtyeight')


In [3]:
df_bill_amount = pd.read_csv('./Healthcare Data Challenge Data/bill_amount.csv')
df_bill_id = pd.read_csv('./Healthcare Data Challenge Data/bill_id.csv')
df_clinical_data = pd.read_csv('./Healthcare Data Challenge Data/clinical_data.csv')
df_demographics = pd.read_csv('./Healthcare Data Challenge Data/demographics.csv')

In [4]:
print(df_bill_amount.info())
print('\n')
print(df_bill_id.info())
print('\n')
print(df_clinical_data.info())
print('\n')
print(df_demographics.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13600 entries, 0 to 13599
Data columns (total 2 columns):
 #   Column   Non-Null Count  Dtype  
---  ------   --------------  -----  
 0   bill_id  13600 non-null  int64  
 1   amount   13600 non-null  float64
dtypes: float64(1), int64(1)
memory usage: 212.6 KB
None


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13600 entries, 0 to 13599
Data columns (total 3 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   bill_id            13600 non-null  int64 
 1   patient_id         13600 non-null  object
 2   date_of_admission  13600 non-null  object
dtypes: int64(1), object(2)
memory usage: 318.9+ KB
None


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3400 entries, 0 to 3399
Data columns (total 26 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   id                  3400 non-null   object 
 1   date_of_admission   

In [5]:
print(df_bill_amount.nunique())
print('\n')
print(df_bill_id.nunique())
print('\n')
print(df_clinical_data.nunique())
print('\n')
print(df_demographics.nunique())

bill_id    13600
amount     13595
dtype: int64


bill_id              13600
patient_id            3000
date_of_admission     1450
dtype: int64


id                    3000
date_of_admission     1450
date_of_discharge     1532
medical_history_1        2
medical_history_2        2
medical_history_3        4
medical_history_4        2
medical_history_5        2
medical_history_6        2
medical_history_7        2
preop_medication_1       2
preop_medication_2       2
preop_medication_3       2
preop_medication_4       2
preop_medication_5       2
preop_medication_6       2
symptom_1                2
symptom_2                2
symptom_3                2
symptom_4                2
symptom_5                2
lab_result_1            98
lab_result_2           148
lab_result_3            90
weight                 522
height                  35
dtype: int64


patient_id         3000
gender                4
race                  6
resident_status       4
date_of_birth      2746
dtype: int64


### Joining `df_bill_amount` and `df_bill_id` dataframes into 1 dataframe `df_comb1`
- as there is a common column `bill_id`, we join based on this column
- there are also the same set of unique `bill_id` numbers between the 2 columns, hence we can proceed with joining the 2 dataframes
- there are also no null values in either dataframes

In [6]:
df_bill_amount.columns
len(df_bill_amount)
df_bill_amount.isnull().sum()

bill_id    0
amount     0
dtype: int64

In [7]:
df_bill_id.columns
len(df_bill_id)
df_bill_id.isnull().sum()

bill_id              0
patient_id           0
date_of_admission    0
dtype: int64

In [8]:
set(df_bill_id['bill_id']) == set(df_bill_amount['bill_id'])

True

In [9]:
df_comb1 = pd.merge(df_bill_amount, df_bill_id, on='bill_id') 
df_comb1.head()

bill_id       amount                        patient_id date_of_admission
0    40315104  1552.634830  96a76ec5bbcb1d1562c40b9b972e356d        2012-10-22
1  2660045161  1032.011951  796de06efdad342d3f3a379dff0bd63c        2014-09-28
2  1148334643  6469.605351  1ce104904e9160cf3cfdb3c45b9ce4ff        2014-01-16
3  3818426276   755.965425  afdfe7216d84e13708a19cbca288379a        2013-01-22
4  9833541918   897.347816  b9a0c119dc07e07f88281964f3a4869f        2011-04-22

In [10]:
df_comb1.dtypes
df_comb1['date_of_admission'] = pd.to_datetime(df_comb1['date_of_admission'])
df_comb1 = df_comb1.astype({
    'bill_id':object,
})
df_comb1.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 13600 entries, 0 to 13599
Data columns (total 4 columns):
 #   Column             Non-Null Count  Dtype         
---  ------             --------------  -----         
 0   bill_id            13600 non-null  object        
 1   amount             13600 non-null  float64       
 2   patient_id         13600 non-null  object        
 3   date_of_admission  13600 non-null  datetime64[ns]
dtypes: datetime64[ns](1), float64(1), object(2)
memory usage: 531.2+ KB


In [11]:
# check for duplicated patient_id
df_comb1[df_comb1.duplicated(subset=['patient_id'], keep=False)].sort_values(by='patient_id')

bill_id        amount                        patient_id  \
4760   5175703971     79.496707  00225710a878eff524a1d13be817e8e2   
1358   4692776325    325.319345  00225710a878eff524a1d13be817e8e2   
12021  7746811189   3710.864731  00225710a878eff524a1d13be817e8e2   
1803   8461069832   1074.885913  00225710a878eff524a1d13be817e8e2   
13123  3604841170    416.161130  0029d90eb654699c18001c17efb0f129   
3537   5621737529   4821.368753  0029d90eb654699c18001c17efb0f129   
5603   5041212157    903.249320  0029d90eb654699c18001c17efb0f129   
1591    645202091  16460.718669  0029d90eb654699c18001c17efb0f129   
10029  7549837665    722.207224  0040333abd68527ecb53e1db9073f52e   
6785   9921582850   1880.154553  0040333abd68527ecb53e1db9073f52e   
8018    167943546    640.269335  0040333abd68527ecb53e1db9073f52e   
6553   8199801360  14204.550522  0040333abd68527ecb53e1db9073f52e   
6585   5492890584   4819.283485  00473b58e3dc8ae37b3cb34069705083   
3096   3108812506    676.420105  00473b58e3dc8ae37b3cb34069705083   
5549   2831040803    584.562386  00473b58e3dc8ae37b3cb34069705083   
6612   7239419545   9205.617244  00473b58e3dc8ae37b3cb34069705083   
9639   4580228676   1517.659366  0078662d1d983dde68ea057c42d5b5cf   
4505   7289756776   3488.225150  0078662d1d983dde68ea057c42d5b5cf   
10830  6208929668  13460.623696  0078662d1d983dde68ea057c42d5b5cf   
6022   9476531069  55011.360798  0078662d1d983dde68ea057c42d5b5cf   
6750   9839868745  20648.066701  0088bbd94c90bbc9158e13465441ebb6   
6470   2127692752   2038.170417  0088bbd94c90bbc9158e13465441ebb6   
11723  8244828782   1273.535127  0088bbd94c90bbc9158e13465441ebb6   
6626   3073145832   2091.820013  0088bbd94c90bbc9158e13465441ebb6   
2737   8770011184  16630.731606  0092d20dd0719e88ecfdd02d5e7ca7b7   
11870  7555504451   1597.993744  0092d20dd0719e88ecfdd02d5e7ca7b7   
12913  6475640623   2079.531729  0092d20dd0719e88ecfdd02d5e7ca7b7   
245    5424397887   1190.729679  0092d20dd0719e88ecfdd02d5e7ca7b7   
11017  5844244730  23414.776514  01081b8bcb0f9e27b888d23bb35a50dd   
11470  7007823815    802.947142  01081b8bcb0f9e27b888d23bb35a50dd   
2459   6244235693   1693.403885  01081b8bcb0f9e27b888d23bb35a50dd   
1457   1089361296   1601.146422  01081b8bcb0f9e27b888d23bb35a50dd   
5351   8607700723   4443.270861  010cf28233f50d3857b499a9c208c610   
3686   4981329240    946.668434  010cf28233f50d3857b499a9c208c610   
13397   651097071  18950.254972  010cf28233f50d3857b499a9c208c610   
5706    640478757   1272.169881  010cf28233f50d3857b499a9c208c610   
6111   8739043589    326.749327  0116c5d9b6c2c2e8758c75e6da86014b   
8921   8403878820   4252.673108  0116c5d9b6c2c2e8758c75e6da86014b   
3426     82234756  10180.021551  0116c5d9b6c2c2e8758c75e6da86014b   
12948  2466575499   1031.153759  0116c5d9b6c2c2e8758c75e6da86014b   
4304   6982890522  24636.548608  011f6ed96aa8a4047a7dc66219db4cd7   
9704   5520138985   1576.311079  011f6ed96aa8a4047a7dc66219db4cd7   
10061  7634961393   1631.324198  011f6ed96aa8a4047a7dc66219db4cd7   
1239   1414629019   2066.490320  011f6ed96aa8a4047a7dc66219db4cd7   
5783   5062243503  13835.663752  012c5eb5397a72f8aeb64f942b60846d   
8509   9951536829   1094.090624  012c5eb5397a72f8aeb64f942b60846d   
12789  1595230701   1818.902499  012c5eb5397a72f8aeb64f942b60846d   
11151  8573149856   1624.137677  012c5eb5397a72f8aeb64f942b60846d   
13274  3385626862    894.156778  012c5eb5397a72f8aeb64f942b60846d   
11179  1475841641   5144.940194  012c5eb5397a72f8aeb64f942b60846d   
3637   5354388962   4926.049428  012c5eb5397a72f8aeb64f942b60846d   
808    6772496454  22627.660498  012c5eb5397a72f8aeb64f942b60846d   
5473   5695041134   1300.111993  01552a3f5a9c868e6e2b2c15553dbd4a   
9850    121109302   3677.491484  01552a3f5a9c868e6e2b2c15553dbd4a   
7787   9154416549   7869.437361  01552a3f5a9c868e6e2b2c15553dbd4a   
4600   3853043059   1293.424086  01552a3f5a9c868e6e2b2c15553dbd4a   
6908   6182924425   1413.901820  015e6ca145eb3aa52dd68440e98c9ea9   
10845  6

In [12]:
for i in df_comb1.columns:
    print(f"{i}: {len(set(df_comb1[i]))}")

bill_id: 13600
amount: 13595
patient_id: 3000
date_of_admission: 1450


Looking at the dataframe above, we can see that there are multiple bills given to the same patient on the same date_of_admission
- this could be due to the way invoices are created in the hospital.
There are 1450 unique `date_of_admissions` over 3000 unique `patient_id`
- this means that there are multiple bills (different `bill_id`) on the same `date_of_admissions` and the same `patient_id`
- also there are 3000 unique `patient_id` but 3400 different patient_id
- hence we groupby using `date_of_admissions` and `patient_id` for better clarity in the amount

In [13]:
df_comb1 = df_comb1.groupby(['patient_id', 'date_of_admission']).sum()
df_comb1 = df_comb1.sort_values(by='patient_id', ascending=False)

### Joining `df_clinical_data` and `df_demographics` dataframes into 1 dataframe `df_comb2`

In [14]:
set(df_clinical_data['id']) == set(df_demographics['patient_id'])

True

- Checking that `df_clinical_data['id']` and `df_demographics['patient_id']` have the same unique set of id. 
- The result above found to be True which means both columns have same unique set of id, hence we can proceed with joining the 2 df below.
- As `df_clinical_data` has more rows than `df_demographics`, we do a left join, where left df is `df_clinical_date`.

In [15]:
df_clinical_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3400 entries, 0 to 3399
Data columns (total 26 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   id                  3400 non-null   object 
 1   date_of_admission   3400 non-null   object 
 2   date_of_discharge   3400 non-null   object 
 3   medical_history_1   3400 non-null   int64  
 4   medical_history_2   3167 non-null   float64
 5   medical_history_3   3400 non-null   object 
 6   medical_history_4   3400 non-null   int64  
 7   medical_history_5   3096 non-null   float64
 8   medical_history_6   3400 non-null   int64  
 9   medical_history_7   3400 non-null   int64  
 10  preop_medication_1  3400 non-null   int64  
 11  preop_medication_2  3400 non-null   int64  
 12  preop_medication_3  3400 non-null   int64  
 13  preop_medication_4  3400 non-null   int64  
 14  preop_medication_5  3400 non-null   int64  
 15  preop_medication_6  3400 non-null   int64  
 16  sympto

In [16]:
df_demographics.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3000 entries, 0 to 2999
Data columns (total 5 columns):
 #   Column           Non-Null Count  Dtype 
---  ------           --------------  ----- 
 0   patient_id       3000 non-null   object
 1   gender           3000 non-null   object
 2   race             3000 non-null   object
 3   resident_status  3000 non-null   object
 4   date_of_birth    3000 non-null   object
dtypes: object(5)
memory usage: 117.3+ KB


In [17]:
df_comb2 = pd.merge(df_clinical_data, df_demographics, how='left', left_on='id', right_on='patient_id')
df_comb2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3400 entries, 0 to 3399
Data columns (total 31 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   id                  3400 non-null   object 
 1   date_of_admission   3400 non-null   object 
 2   date_of_discharge   3400 non-null   object 
 3   medical_history_1   3400 non-null   int64  
 4   medical_history_2   3167 non-null   float64
 5   medical_history_3   3400 non-null   object 
 6   medical_history_4   3400 non-null   int64  
 7   medical_history_5   3096 non-null   float64
 8   medical_history_6   3400 non-null   int64  
 9   medical_history_7   3400 non-null   int64  
 10  preop_medication_1  3400 non-null   int64  
 11  preop_medication_2  3400 non-null   int64  
 12  preop_medication_3  3400 non-null   int64  
 13  preop_medication_4  3400 non-null   int64  
 14  preop_medication_5  3400 non-null   int64  
 15  preop_medication_6  3400 non-null   int64  
 16  sympto

In [18]:
for i in df_comb2.columns:
    print(f"{i}: {len(set(df_comb2[i]))}")

id: 3000
date_of_admission: 1450
date_of_discharge: 1532
medical_history_1: 2
medical_history_2: 235
medical_history_3: 4
medical_history_4: 2
medical_history_5: 306
medical_history_6: 2
medical_history_7: 2
preop_medication_1: 2
preop_medication_2: 2
preop_medication_3: 2
preop_medication_4: 2
preop_medication_5: 2
preop_medication_6: 2
symptom_1: 2
symptom_2: 2
symptom_3: 2
symptom_4: 2
symptom_5: 2
lab_result_1: 98
lab_result_2: 148
lab_result_3: 90
weight: 522
height: 35
patient_id: 3000
gender: 4
race: 6
resident_status: 4
date_of_birth: 2746


In [19]:
temps = df_comb2['patient_id'].value_counts()
for i in set(temps):
    print(f"unique patients with {i} visit : {list(temps).count(i)}")

unique patients with 1 visit : 2621
unique patients with 2 visit : 359
unique patients with 3 visit : 19
unique patients with 4 visit : 1


There were 379 patients with more than 1 visit.

In [20]:
pd.set_option('display.max_columns', 10)
pd.set_option('display.max_rows', 10)

for col in df_comb2.columns:
    print(df_comb2[col].value_counts())
    print('\n')

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

4e46fddfa404b306809c350aecbf0f6a    4
feb52392f4d58a02254cbd0ba634312f    3
6a6991ecb85a2f82f77b09eb0eeb747b    3
af713a949eda293f348bf51a058e48a1    3
258807316af4b45fda1b05668d557d06    3
                                   ..
a1a3bc72b1ace18f431d015ef1c2f2af    1
507146bde02748a71ba5cee4f3553e81    1
9d3797ef50b01dc5a04de56cbdad7392    1
598aecafdbee970006edea2be9006155    1
b26f39a09c02398bce00cb36687c5e98    1
Name: id, Length: 3000, dtype: int64


2014-05-24    9
2012-10-14    7
2014-05-21    7
2012-08-19    7
2012-06-26    7
             ..
2012-09-05    1
2015-07-11    1
2013-12-21    1
2011-01-24    1
2013-03-14    1
Name: date_of_admission, Length: 1450, dtype: int64


2011-10-23    9
2013-11-28    7
2012-06-04    7
2012-03-11    7
2014-03-04    7
             ..
2015-09-27    1
2014-10-24    1
2015-01-05    1
2013-10-09    1
2011-09-03    1
Name: date_of_discharge, Length: 1532, dtype: int64


0    2825
1     575
Name: medical_history_1, dtype: int64


0.0    2181
1.0     986

From the above, we can see that some columns have inconsistent values, hence we change this values to more consistent values in the next step.

### Changing values to keep consistency within each column

In [21]:
df_comb2['medical_history_3'].replace({'No':0,'Yes':1}, inplace=True)
df_comb2['gender'].replace({'f':'Female', 'm':'Male'}, inplace=True)
df_comb2['race'].replace({'chinese':'Chinese','India':'Indian'}, inplace=True)
df_comb2['resident_status'].replace({'Singapore citizen':'Singaporean','India':'Indian'}, inplace=True)

### Change data types of columns 
- converting float to int for boolean value columns
- converting object to datetime for datetime columns

In [22]:
df_comb2.dtypes
df_comb2 = df_comb2.astype({
#     'medical_history_2': int,
    'medical_history_3': int,
#     'medical_history_5': int,
})

df_comb2['date_of_admission'] = pd.to_datetime(df_comb2['date_of_admission'])
df_comb2['date_of_discharge'] = pd.to_datetime(df_comb2['date_of_discharge'])
df_comb2['date_of_birth'] = pd.to_datetime(df_comb2['date_of_birth'])

### Feature engineering columns

In [23]:
df_comb2['age'] = ((df_comb2['date_of_admission'].dt.year*12 + df_comb2['date_of_admission'].dt.month) - \
            (df_comb2['date_of_birth'].dt.year*12 + df_comb2['date_of_birth'].dt.month))/12

df_comb2['duration(days)'] = df_comb2['date_of_discharge'] - df_comb2['date_of_admission']
df_comb2['duration(days)'] = df_comb2['duration(days)'].dt.days

In [24]:
len(df_comb2.columns)

33

In [25]:
df_comb2 = df_comb2[['patient_id', 'date_of_admission', 'date_of_discharge', 'date_of_birth' ,'weight', 
            'height', 'gender', 'race', 'resident_status','age', 'duration(days)', 'medical_history_1',
           'medical_history_2', 'medical_history_3', 'medical_history_4',
           'medical_history_5', 'medical_history_6', 'medical_history_7',
           'preop_medication_1', 'preop_medication_2', 'preop_medication_3',
           'preop_medication_4', 'preop_medication_5', 'preop_medication_6',
           'symptom_1', 'symptom_2', 'symptom_3', 'symptom_4', 'symptom_5',
           'lab_result_1', 'lab_result_2', 'lab_result_3']]

In [26]:
len(df_comb2.columns)

32

### Null values

In [27]:
med_2 = np.round(df_comb2['medical_history_2'].isnull().sum()/len(df_comb2)*100, 2)
med_5 = np.round(df_comb2['medical_history_5'].isnull().sum()/len(df_comb2)*100, 2)
pct = np.round(len(df_comb2[df_comb2['medical_history_2'].isnull() | df_comb2['medical_history_5'].isnull()])
               /len(df_comb2)*100,2)

print(f'{med_2}% of values in medical_history_2 column are null values')
print(f'{med_5}% of values in medical_history_5 column are null values')
print(f'{pct}% of rows in df_comb2 has at least 1 null value')


6.85% of values in medical_history_2 column are null values
8.94% of values in medical_history_5 column are null values
14.76% of rows in df_comb2 has at least 1 null value


- checking for null values, we found that `medical_history_2` and `medical_history_5` have 233 and 304 null values respectively. 
- as the proportion of null values are substantially large, we do not drop these columns.
- null values will be kept for the time being so that we can account for them during visualization

___

### Joining `df_comb1` and `df_comb2` into 1 dataframe `df`
- we join based on `patient_id` and `date_of_admission` column since it is the common column

In [28]:
df_comb1 = df_comb1.reset_index()

In [29]:
set(df_comb1.patient_id)==set(df_comb2.patient_id)

True

In [30]:
df = pd.merge(df_comb1, df_comb2, on=['patient_id','date_of_admission'], how='outer', indicator=True)
# df = pd.merge(df_comb1, df_comb2, on=['patient_id'], how='left', indicator=True)

df.isnull().sum()
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3400 entries, 0 to 3399
Data columns (total 34 columns):
 #   Column              Non-Null Count  Dtype         
---  ------              --------------  -----         
 0   patient_id          3400 non-null   object        
 1   date_of_admission   3400 non-null   datetime64[ns]
 2   amount              3400 non-null   float64       
 3   date_of_discharge   3400 non-null   datetime64[ns]
 4   date_of_birth       3400 non-null   datetime64[ns]
 5   weight              3400 non-null   float64       
 6   height              3400 non-null   float64       
 7   gender              3400 non-null   object        
 8   race                3400 non-null   object        
 9   resident_status     3400 non-null   object        
 10  age                 3400 non-null   float64       
 11  duration(days)      3400 non-null   int64         
 12  medical_history_1   3400 non-null   int64         
 13  medical_history_2   3167 non-null   float64     

In [31]:
df.head()

patient_id date_of_admission        amount  \
0  ffd9644f8daf1d28493a7cd700bb30f4        2013-06-04  21040.661990   
1  ffd67c2bcfb32508d2cf7b1e1193e2ed        2012-12-24  28007.636468   
2  ffc19537fa6621512ef4f296d60896ce        2013-05-05  30053.620971   
3  ffac3c4b6838f42625e1dd00dd7c867b        2015-11-28  14049.042774   
4  ffa5a615a4cc5fb1ada0443edc1f5dd3        2011-04-24   4676.066179   

  date_of_discharge date_of_birth  weight  height  gender     race  \
0        2013-06-15    1956-04-02    70.7   165.0  Female  Chinese   
1        2013-01-01    1950-06-06    81.3   161.0    Male    Malay   
2        2013-05-15    1938-09-12    83.1   170.0    Male  Chinese   
3        2015-12-07    1963-10-07    99.6   178.0    Male  Chinese   
4        2011-05-04    1976-08-07    69.3   162.0  Female   Indian   

  resident_status        age  duration(days)  medical_history_1  \
0     Singaporean  57.166667              11                  0   
1     Singaporean  62.500000               8                  0   
2              PR  74.666667              10                  0   
3     Singaporean  52.083333               9                  0   
4     Singaporean  34.666667              10                  0   

   medical_history_2  medical_history_3  medical_history_4  medical_history_5  \
0                0.0                  0                  0                0.0   
1                0.0                  0                  0                0.0   
2                1.0                  0                  0                1.0   
3                0.0                  0                  0                0.0   
4                1.0                  0                  0                0.0   

   medical_history_6  medical_history_7  preop_medication_1  \
0                  0                  1                   0   
1                  0                  0                   1   
2                  0                  0                   1   
3                  0                  0                   1   
4                  0                  1                   0   

   preop_medication_2  preop_medication_3  preop_medication_4  \
0                   0                   1                   1   
1                   1                   1                   1   
2                   1                   1                   1   
3                   1                   1                   1   
4                   0                   1                   0   

   preop_medication_5  preop_medication_6  symptom_1  symptom_2  symptom_3  \
0                   1                   1          1          0          1   
1                   1                   0          1          1          1   
2                   1                   1          0          0          1   
3                   1                   1          1          1          0   
4                   1                   0          0          0          0   

   symptom_4  symptom_5  lab_result_1  lab_result_2  lab_result_3 _merge  
0          1          1          13.9          26.9          95.0   both  
1          1          0          16.4          33.6          96.0   both  
2          1          1          16.7          30.1         107.0   both  
3          1          0          16.0          26.7         121.0   both  
4          0          0          16.3          27.4          86.0   both

### export cleaned dataframe into `.csv` for data analysis and visualisation

In [32]:
df.to_csv('df_cleaned', index=False)